# Prepare data before building train/test data for baseline model

### NOTE: 
Step 4 - Building X_train, Y_train, X_test, Y_Test will be performed in a separate task due to long time for computation. (Last attempt crashes after > 15 hours running for generating X_train)

Load dataset extracted from step 3 and re-perform TF-IDF.

### SUMMARY:
- Source: [Repository PJFNN](https://github.com/doslim/Job-Recommendation-PJFNN) 
- Input: Clean dataset 
    - users_clean.csv
    - jobset_clean.csv
    - work_history.csv
    - dataset.csv
- Summary:
    - TF-IDF on jobs data (Corpus: job title + description + requirement)
    - TF-IDF on work_history data (Corpus: job titles linked to one user) => work_history_cleaned.csv
    - Label encoding for some columns in user data => user_set_cleaned.csv
    - Match country, state, and city between user and job in the interaction data (dataset) => dataset_cleaned.csv 
    - DROP duplicated data in dataset to avoid error when building feature vector (See the debug section 4)
- Output:
    - user_set_cleaned.csv
    - work_history_cleaned.csv
    - dataset_cleaned.csv

In [ ]:
import caffeine
caffeine.on(display=False)

In [ ]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from tqdm import tqdm

In [ ]:
# Load pre-processed data
path = "./data_processed/"
user_set = pd.read_csv(path +"users_clean.csv")
job_set = pd.read_csv(path + "jobset_clean.csv")
work_history = pd.read_csv(path + "work_history.csv") 
dataset = pd.read_csv(path + "dataset.csv") #negative sampling application data

/var/folders/rt/sq9c2fwj2wz441h13l9hcfrc0000gn/T/ipykernel_3297/3598351642.py:4: DtypeWarning: Columns (8) have mixed types. Specify dtype option on import or set low_memory=False.
  job_set = pd.read_csv(path + "jobset_clean.csv")


In [ ]:
user_set.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 258260 entries, 0 to 258259
Data columns (total 15 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   UserID                258260 non-null  int64  
 1   WindowID              258260 non-null  int64  
 2   Split                 258260 non-null  object 
 3   City                  258260 non-null  object 
 4   State                 257917 non-null  object 
 5   Country               258260 non-null  object 
 6   ZipCode               257094 non-null  object 
 7   DegreeType            258260 non-null  object 
 8   Major                 258260 non-null  object 
 9   GraduationDate        203034 non-null  object 
 10  WorkHistoryCount      258260 non-null  int64  
 11  TotalYearsExperience  258260 non-null  float64
 12  CurrentlyEmployed     258260 non-null  object 
 13  ManagedOthers         258260 non-null  object 
 14  ManagedHowMany        258260 non-null  int64  
dtype

In [ ]:
job_set.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1050509 entries, 0 to 1050508
Data columns (total 11 columns):
 #   Column        Non-Null Count    Dtype 
---  ------        --------------    ----- 
 0   JobID         1050509 non-null  int64 
 1   WindowID      1050509 non-null  int64 
 2   Title         1050509 non-null  object
 3   Description   1050289 non-null  object
 4   Requirements  1047776 non-null  object
 5   City          1050507 non-null  object
 6   State         1050508 non-null  object
 7   Country       1050506 non-null  object
 8   Zip5          658844 non-null   object
 9   StartDate     1050509 non-null  object
 10  EndDate       1050500 non-null  object
dtypes: int64(2), object(9)
memory usage: 88.2+ MB


In [ ]:
work_history.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1144557 entries, 0 to 1144556
Data columns (total 5 columns):
 #   Column    Non-Null Count    Dtype 
---  ------    --------------    ----- 
 0   UserID    1144557 non-null  int64 
 1   WindowID  1144557 non-null  int64 
 2   Split     1144557 non-null  object
 3   Sequence  1144557 non-null  int64 
 4   JobTitle  1144557 non-null  object
dtypes: int64(3), object(2)
memory usage: 43.7+ MB


In [ ]:
dataset.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2081340 entries, 0 to 2081339
Data columns (total 3 columns):
 #   Column  Dtype
---  ------  -----
 0   UserID  int64
 1   JobID   int64
 2   label   int64
dtypes: int64(3)
memory usage: 47.6 MB


# 1. TF-IDF vectors for text representation for jobs
- word: combine job Title, Description, and Requirement
- TF-IDF on word

In [ ]:
# Create corpus by joining job Title, Description, and Requirement
job_set = job_set.fillna(" ")
job_set["word"] = job_set.Title + job_set.Description + job_set.Requirements

In [ ]:
job_set.word.head()

0    Security Engineer Technical LeadSecurity Clear...
1    SAP Business Analyst   WMNO Corp. to Corp resu...
2    P T HUMAN RESOURCES ASSISTANT     P T HUMAN RE...
3    Route Delivery DriversCITY BEVERAGES Come to w...
4    HousekeepingI make  sure every part of their d...
Name: word, dtype: object

In [ ]:
import time
start = time.time()
    
# TF-IDF on the combination of Title & Description & Requirements
tf = TfidfVectorizer(analyzer='word',
                     ngram_range=(1, 2),
                     min_df=5, 
                     max_features=100, 
                     stop_words='english')
tfidf_matrix = tf.fit_transform(job_set['word'])

end = time.time()
print('Computing time: ', end - start)

Computing time:  632.002653837204


# 2. Filter out users with more than 10 applications

In [ ]:
# Input: application data after negative sampling
temp = sorted(dict(dataset.UserID.value_counts()).items(), key=lambda x: x[1], reverse=True)
exclude_user_id = [i[0] for i in temp if i [1]>=10]
len(exclude_user_id)

56661

In [ ]:
# Drop application where user_id is in exclude list
dataset = dataset[~dataset.UserID.isin(exclude_user_id)] 

In [ ]:
dataset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 579626 entries, 0 to 2081339
Data columns (total 3 columns):
 #   Column  Non-Null Count   Dtype
---  ------  --------------   -----
 0   UserID  579626 non-null  int64
 1   JobID   579626 non-null  int64
 2   label   579626 non-null  int64
dtypes: int64(3)
memory usage: 17.7 MB


### select data in ```work_history, user_set```

In [ ]:
user_id = dataset.UserID.unique()
work_history = work_history[work_history.UserID.isin(user_id)]
user_set = user_set[user_set.UserID.isin(user_id)]
user_set.reset_index(drop=True, inplace=True)

### drop duplicates in ```work_history```

In [ ]:
work_history.duplicated(subset=['Sequence']).value_counts()

True     683435
False       119
dtype: int64

In [ ]:
work_history = work_history.drop(columns=["Sequence"]).drop_duplicates()

In [ ]:
work_history.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 628173 entries, 8 to 1144555
Data columns (total 4 columns):
 #   Column    Non-Null Count   Dtype 
---  ------    --------------   ----- 
 0   UserID    628173 non-null  int64 
 1   WindowID  628173 non-null  int64 
 2   Split     628173 non-null  object
 3   JobTitle  628173 non-null  object
dtypes: int64(2), object(2)
memory usage: 24.0+ MB


In [ ]:
word_history_tf = TfidfVectorizer(analyzer='word',
                                  ngram_range=(1, 2),
                                  min_df=0, 
                                  max_features=50, 
                                  stop_words='english')

In [ ]:
# Get all the title that one user have applied
work_history.groupby("UserID").JobTitle.sum().values

array(['Front End Supervisor/CashierCustomer Service Representative',
       'CookMechanicFile Clerk',
       'Pennsylvania MentorStudent WorkerInternship in Adoption UnitStudent Worker - Continuing EducationSales Associate',
       ...,
       'Front Office ManagerAt Your Service SupervisorFront Desk SupervisorOperations SupervisorReservations CoordinatorFront Desk Agent',
       'Preschool TeacherSalesCustomer Service',
       'ElectricianTechnicianSupervisorElectrician (trainee)'],
      dtype=object)

In [ ]:
# Apply TF-IDF on all previous job title of a user
word_history_tf_matrix = word_history_tf \
                        .fit_transform(work_history \
                                       .groupby("UserID") \
                                       .JobTitle.sum().values)

In [ ]:
word_history_tf_matrix

<152292x50 sparse matrix of type '<class 'numpy.float64'>'
	with 327656 stored elements in Compressed Sparse Row format>

# 3. 1 Deal with the user set

In [ ]:
user_set.info() # 152,292

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 152292 entries, 0 to 152291
Data columns (total 15 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   UserID                152292 non-null  int64  
 1   WindowID              152292 non-null  int64  
 2   Split                 152292 non-null  object 
 3   City                  152292 non-null  object 
 4   State                 152078 non-null  object 
 5   Country               152292 non-null  object 
 6   ZipCode               151609 non-null  object 
 7   DegreeType            152292 non-null  object 
 8   Major                 152292 non-null  object 
 9   GraduationDate        119399 non-null  object 
 10  WorkHistoryCount      152292 non-null  int64  
 11  TotalYearsExperience  152292 non-null  float64
 12  CurrentlyEmployed     152292 non-null  object 
 13  ManagedOthers         152292 non-null  object 
 14  ManagedHowMany        152292 non-null  int64  
dtype

In [ ]:
user_set.Country.value_counts()

US    151814
IN        87
CA        47
MX        34
PH        32
       ...  
IQ         1
LU         1
CY         1
DK         1
GA         1
Name: Country, Length: 82, dtype: int64

In [ ]:
user_set[user_set['Country'] != "US"].count()

UserID                  478
WindowID                478
Split                   478
City                    478
State                   264
Country                 478
ZipCode                   5
DegreeType              478
Major                   478
GraduationDate          417
WorkHistoryCount        478
TotalYearsExperience    478
CurrentlyEmployed       478
ManagedOthers           478
ManagedHowMany          478
dtype: int64

In [ ]:
# Change compare to original repository: do not filter only for user in the US 
# => Keep column "Country"
user_set = user_set.drop(columns=["ZipCode","Major","GraduationDate","WindowID"])

In ```user_set``` 
- label encoding for ```DegreeType```
- one-hot encoding for ```State```
- binary labels for Currently ```Employed/ManagedOthers```

In [ ]:
# user_set = pd.get_dummies(user_set, columns=["State"])
user_set.replace({"CurrentlyEmployed":{"Yes":1,"No":0}}, inplace=True)
user_set.replace({"ManagedOthers":{"Yes":1,"No":0}}, inplace=True)
user_set.replace({"DegreeType":{"None":0,"High School":1, "Vocational":2, "Associate's":3, "Bachelor's":4, "Master's":5, "PhD":6}}, 
                 inplace=True)

In [ ]:
user_set

UserID  Split           City State Country  DegreeType  \
0            80  Train   Williamstown    NJ      US           1   
1           123  Train    Baton Rouge    LA      US           4   
2           162  Train     Long Beach    CA      US           5   
3           178  Train     Greenville    SC      US           1   
4           344  Train   Newport News    VA      US           1   
...         ...    ...            ...   ...     ...         ...   
152287  1471706  Train         Baxter    MN      US           1   
152288  1471870  Train        Lubbock    TX      US           0   
152289  1471878  Train     Orangeburg    SC      US           1   
152290  1471997  Train      Baltimore    MD      US           1   
152291  1472060  Train  Lawrenceville    GA      US           1   

        WorkHistoryCount  TotalYearsExperience  CurrentlyEmployed  \
0                      5                  11.0                  1   
1                      1                   9.0                  1   
2                     10                  25.0                  0   
3                      6                  35.0                  0   
4                      3                   7.0                  1   
...                  ...                   ...                ...   
152287                 5                  21.0                  1   
152288                 5                  19.0                  0   
152289                 4                   3.0                  0   
152290                 3                   5.0                  0   
152291                 3                   1.0                  0   

        ManagedOthers  ManagedHowMany  
0                   1               5  
1                   0               0  
2                   0               0  
3                   1               4  
4                   0               0  
...               ...             ...  
152287              0               0  
152288              0               0  
152289              0               0  
152290              1              45  
152291              0               0  

[152292 rows x 11 columns]

# 3.2. Add binary columns in "dataset" to match city, state, and country between users and jobs

- add binary labels into the dataset, indicating that whether the user and job are in the same country/city/state. (add country match)

In [ ]:
# Test on small sample (2 users)
country = []
city = []
state = []
groups = dataset.groupby("UserID")
users_check = []

for idx, group in tqdm(groups):
       
    print('applications by user: ', idx, group)
    
    user_city = user_set[user_set.UserID==idx]["City"].values
    user_state = user_set[user_set.UserID==idx]["State"].values
    user_country = user_set[user_set.UserID==idx]["Country"].values

    job_id_list = group.JobID.values
    job_city = job_set[job_set.JobID.isin(job_id_list)]["City"].values
    job_state = job_set[job_set.JobID.isin(job_id_list)]["State"].values
    job_country = job_set[job_set.JobID.isin(job_id_list)]["Country"].values

    print('len of user_city, state, country: ', len(user_city), len(user_state), len(user_country))
    print('len of job_city, state, country: ', len(job_city), len(job_state), len(job_country))
    print('len of matching list: ', len(user_city)*len(job_city))
    
    city.extend([0 if i!=user_city else 1 for i in job_city])
    state.extend([0 if i!=user_state else 1 for i in job_state])
    country.extend([0 if i!=user_country else 1 for i in job_country])
    
    print('len of new city matching: ', len(city))
    
    users_check.append(idx)
    print('Number of users checked:', len(users_check))
    
    if len(users_check) == 3:
        break
    
    
    

  0%|                                                | 0/152292 [00:00<?, ?it/s]

applications by user:  7    UserID   JobID  label
0       7  309823      1
1       7  703889      1
2       7  566574      0
3       7  481216      0


  0%|                                    | 2/152292 [00:27<576:28:13, 13.63s/it]

len of user_city, state, country:  1 1 1
len of job_city, state, country:  4 4 4
len of matching list:  4
len of new city matching:  4
Number of users checked: 1
applications by user:  9    UserID   JobID  label
4       9  809208      1
5       9  136489      1
6       9  617374      1
7       9  860271      0
8       9  556732      0
9       9  754994      0
len of user_city, state, country:  1 1 1
len of job_city, state, country:  6 6 6
len of matching list:  6
len of new city matching:  10
Number of users checked: 2
applications by user:  13     UserID   JobID  label
10      13  821691      1
11      13  329572      0
len of user_city, state, country:  1 1 1
len of job_city, state, country:  2 2 2
len of matching list:  2
len of new city matching:  12
Number of users checked: 3


In [ ]:
groups.UserID.unique().count()

152292

In [ ]:
# Execution time ~ 30 mins
country = []
city = []
state = []
groups = dataset.groupby("UserID")
users_check = []

for idx, group in tqdm(groups):
    user_city = user_set[user_set.UserID==idx]["City"].values
    user_state = user_set[user_set.UserID==idx]["State"].values
    user_country = user_set[user_set.UserID==idx]["Country"].values
    
    job_id_list = group.JobID.values
    job_city = job_set[job_set.JobID.isin(job_id_list)]["City"].values
    job_state = job_set[job_set.JobID.isin(job_id_list)]["State"].values
    job_country = job_set[job_set.JobID.isin(job_id_list)]["Country"].values
    
    city.extend([0 if i!=user_city else 1 for i in job_city])
    state.extend([0 if i!=user_state else 1 for i in job_state])
    country.extend([0 if i!=user_country else 1 for i in job_country])
    users_check.append(idx)

100%|███████████████████████████████████| 152292/152292 [26:59<00:00, 94.05it/s]


In [ ]:
len(country), len(city), len(state)

(579625, 579625, 579625)

In [ ]:
len(dataset)

579626

In [ ]:
users_check[-1]

1472090

In [ ]:
dataset.iloc[579625]

UserID    1472090
JobID      354025
label           0
Name: 2081339, dtype: int64

In [ ]:
len(country)

579625

In [ ]:
# # Add three binary features to the application data:
# ValueError: Length of values (579725) does not match length of index (579626)

# dataset["Country"] = country
# dataset["City"] = city
# dataset["State"] = state

## Debug: try smaller dataset (100 applications)
No error

In [ ]:
dataset_small = dataset.iloc[:100]

In [ ]:
dataset_small

UserID   JobID  label
0         7  309823      1
1         7  703889      1
2         7  566574      0
3         7  481216      0
4         9  809208      1
..      ...     ...    ...
179     272   90723      1
180     272  752662      1
181     272  575915      0
182     272  726644      0
183     272  157166      0

[100 rows x 3 columns]

In [ ]:
# Try on subset of dataset (100 applications)
country_small = []
city_small = []
state_small = []
groups_small = dataset_small.groupby("UserID")
users_check_small = []

for idx, group in tqdm(groups_small):
    user_city = user_set[user_set.UserID==idx]["City"].values
    user_state = user_set[user_set.UserID==idx]["State"].values
    user_country = user_set[user_set.UserID==idx]["Country"].values
    
    job_id_list = group.JobID.values
    job_city = job_set[job_set.JobID.isin(job_id_list)]["City"].values
    job_state = job_set[job_set.JobID.isin(job_id_list)]["State"].values
    job_country = job_set[job_set.JobID.isin(job_id_list)]["Country"].values
    
    city_small.extend([0 if i!=user_city else 1 for i in job_city])
    state_small.extend([0 if i!=user_state else 1 for i in job_state])
    country_small.extend([0 if i!=user_country else 1 for i in job_country])
    users_check_small.append(idx)

100%|███████████████████████████████████████████| 29/29 [00:00<00:00, 75.99it/s]


In [ ]:
dataset_small["Country"] = country_small
dataset_small["City"] = city_small
dataset_small["State"] = state_small

/var/folders/rt/sq9c2fwj2wz441h13l9hcfrc0000gn/T/ipykernel_3297/3710079621.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataset_small["Country"] = country_small
/var/folders/rt/sq9c2fwj2wz441h13l9hcfrc0000gn/T/ipykernel_3297/3710079621.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataset_small["City"] = city_small
/var/folders/rt/sq9c2fwj2wz441h13l9hcfrc0000gn/T/ipykernel_3297/3710079621.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using

In [ ]:
dataset_small

UserID   JobID  label  Country  City  State
0         7  309823      1        1     0      0
1         7  703889      1        1     1      1
2         7  566574      0        1     1      1
3         7  481216      0        1     0      0
4         9  809208      1        1     0      0
..      ...     ...    ...      ...   ...    ...
179     272   90723      1        1     0      0
180     272  752662      1        1     0      0
181     272  575915      0        1     0      1
182     272  726644      0        1     0      1
183     272  157166      0        1     0      1

[100 rows x 6 columns]

In [ ]:
len(users_check_small)

29

### Using user defined function and apply on dataset (lambda)

In [ ]:
def get_city_match(user_id, job_id):
    user = user_set[user_set['UserID'] == user_id].iloc[0]
    job = job_set[job_set['JobID'] == job_id].iloc[0]
    return float(user['City'] == job['City'])

In [ ]:
def get_state_match(user_id, job_id):
    user = user_set[user_set['UserID'] == user_id].iloc[0]
    job = job_set[job_set['JobID'] == job_id].iloc[0]
    return float(user['State'] == job['State'])

In [ ]:
def get_country_match(user_id, job_id):
    user = user_set[user_set['UserID'] == user_id].iloc[0]
    job = job_set[job_set['JobID'] == job_id].iloc[0]
    return float(user['Country'] == job['Country'])

In [ ]:
import time
start = time.time()
dataset['City'] = dataset.apply(lambda x: get_city_match(x.UserID, x.JobID), axis=1)
end = time.time()
print('Computing time: ', end - start)

Computing time:  925.5632119178772


In [ ]:
import time
start = time.time()
dataset['State'] = dataset.apply(lambda x: get_state_match(x.UserID, x.JobID), axis=1)
end = time.time()
print('Computing time: ', end - start)

Computing time:  1078.7487421035767


In [ ]:
import time
start = time.time()
dataset['Country'] = dataset.apply(lambda x: get_country_match(x.UserID, x.JobID), axis=1)
end = time.time()
print('Computing time: ', end - start)

Computing time:  1055.5941779613495


In [ ]:
# Check output
dataset.head()

UserID   JobID  label  City  State  Country
0       7  309823      1   1.0    1.0      1.0
1       7  703889      1   1.0    1.0      1.0
2       7  566574      0   0.0    0.0      1.0
3       7  481216      0   0.0    0.0      1.0
4       9  809208      1   1.0    1.0      1.0

## Export data => This will be used for STEP 4: Building training and testing set

In [ ]:
job_set.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1050509 entries, 0 to 1050508
Data columns (total 12 columns):
 #   Column        Non-Null Count    Dtype 
---  ------        --------------    ----- 
 0   JobID         1050509 non-null  int64 
 1   WindowID      1050509 non-null  int64 
 2   Title         1050509 non-null  object
 3   Description   1050509 non-null  object
 4   Requirements  1050509 non-null  object
 5   City          1050509 non-null  object
 6   State         1050509 non-null  object
 7   Country       1050509 non-null  object
 8   Zip5          1050509 non-null  object
 9   StartDate     1050509 non-null  object
 10  EndDate       1050509 non-null  object
 11  word          1050509 non-null  object
dtypes: int64(2), object(10)
memory usage: 96.2+ MB


In [ ]:
job_set.head()

JobID  WindowID                             Title  \
0      1         1  Security Engineer Technical Lead   
1      4         1         SAP Business Analyst   WM   
2      7         1     P T HUMAN RESOURCES ASSISTANT   
3      8         1            Route Delivery Drivers   
4      9         1                      Housekeeping   

                                         Description  \
0  Security Clearance Required:  Top Secret Job N...   
1  NO Corp. to Corp resumes are being considered ...   
2       P T HUMAN RESOURCES ASSISTANT      1-2 ye...   
3  CITY BEVERAGES Come to work for the best in th...   
4  I make  sure every part of their day is magica...   

                                        Requirements         City State  \
0  SKILL SET Network Security tools: Webdefend We...   Washington    DC   
1  WHAT YOU NEED: Four year college degreeMinimum...    Charlotte    NC   
2  Please refer to the Job Description to view th...  Winter Park    FL   
3  Please refer to the Job Description to view th...      Orlando    FL   
4  Please refer to the Job Description to view th...      Orlando    FL   

  Country   Zip5                StartDate              EndDate  \
0      US  20531  2012-03-07 13:17:01.643  2012-04-06 23:59:59   
1      US  28217  2012-03-21 02:03:44.137  2012-04-20 23:59:59   
2      US  32792  2012-03-02 16:36:55.447  2012-04-01 23:59:59   
3      US         2012-03-03 09:01:10.077  2012-04-02 23:59:59   
4      US          2012-03-03 09:01:11.88  2012-04-02 23:59:59   

                                                word  
0  Security Engineer Technical LeadSecurity Clear...  
1  SAP Business Analyst   WMNO Corp. to Corp resu...  
2  P T HUMAN RESOURCES ASSISTANT     P T HUMAN RE...  
3  Route Delivery DriversCITY BEVERAGES Come to w...  
4  HousekeepingI make  sure every part of their d...

In [ ]:
dataset.drop_duplicates(inplace=True, ignore_index=False)

In [ ]:
user_set.to_csv("./data_interim/user_set_cleaned.csv", index=False)
dataset.to_csv("./data_interim/dataset_cleaned.csv", index=False)
work_history.to_csv("./data_interim/work_history_cleaned.csv", index=False)

# DRAFT 4. Build the training set and testing set

In [ ]:
train_user = user_set[user_set.Split=="Train"].UserID.values
test_user = user_set[user_set.Split=="Test"].UserID.values
train_data = dataset[dataset.UserID.isin(train_user)]
test_data = dataset[dataset.UserID.isin(test_user)]

In [ ]:
groups.head()

UserID   JobID  label  City  State  Country
0              7  309823      1   1.0    1.0      1.0
1              7  703889      1   1.0    1.0      1.0
2              7  566574      0   0.0    0.0      1.0
3              7  481216      0   0.0    0.0      1.0
4              9  809208      1   1.0    1.0      1.0
...          ...     ...    ...   ...    ...      ...
2081335  1472085  209482      0   0.0    0.0      1.0
2081336  1472090  209535      1   1.0    1.0      1.0
2081337  1472090  254881      1   1.0    1.0      1.0
2081338  1472090  999294      0   0.0    0.0      1.0
2081339  1472090  354025      0   0.0    0.0      1.0

[494017 rows x 6 columns]

## Start building vectors
2 versions:
- including Country match (vector size: 159)
- excluding Country match (vector size: 158, similar to PJFNN)

# DEBUG - 4. Build the training set and testing set
(The initial dataset has duplication => cause error in concatinate)

In [ ]:
train_user = user_set[user_set.Split=="Train"].UserID.values
test_user = user_set[user_set.Split=="Test"].UserID.values
train_data = dataset[dataset.UserID.isin(train_user)]
test_data = dataset[dataset.UserID.isin(test_user)]

In [ ]:
groups.head()

UserID   JobID  label  City  State  Country
0              7  309823      1   1.0    1.0      1.0
1              7  703889      1   1.0    1.0      1.0
2              7  566574      0   0.0    0.0      1.0
3              7  481216      0   0.0    0.0      1.0
4              9  809208      1   1.0    1.0      1.0
...          ...     ...    ...   ...    ...      ...
2081335  1472085  209482      0   0.0    0.0      1.0
2081336  1472090  209535      1   1.0    1.0      1.0
2081337  1472090  254881      1   1.0    1.0      1.0
2081338  1472090  999294      0   0.0    0.0      1.0
2081339  1472090  354025      0   0.0    0.0      1.0

[507271 rows x 6 columns]

## Debug: user_profile: 50231


In [ ]:
# Try with small iteration

groups = train_data.groupby("UserID")
X_train = np.zeros((1,158))
Y_train = []
mark_stop = 0

for u_id, group in tqdm(groups):
    print(u_id)
    user = user_set[user_set.UserID==u_id][["DegreeType", "WorkHistoryCount", 
                                            "TotalYearsExperience", "CurrentlyEmployed", 
                                            "ManagedOthers", "ManagedHowMany"]]
    print('user profile: ', user)
    
    u_idx = user.index.values[0]
    
    user_feature = np.concatenate((user.values, word_history_tf_matrix[u_idx,:].toarray()),axis=1)
    print('user feature: ', user_feature)
        
    job_id_list = group.JobID.values
    jobs = job_set[job_set.JobID.isin(job_id_list)]
    print('jobs applied by the user: ', job_id_list)
    
    j_idx = jobs.index.values
    f = []
    
    for i in j_idx:
        feature = np.concatenate((user_feature, tfidf_matrix[i,:].toarray()), axis=1).reshape(156,).tolist()
        f.append(feature)
    print('combine user_feature and embeded job', len(f))
    
    feature = np.concatenate((group[["City","State"]].values, np.array(f)),axis=1)
    
    X_train = np.concatenate((X_train, feature), axis=0)
    Y_train.extend(group.label.values.tolist())
    
    print('Result X_train, Y_train:')
    print(X_train)
    print(Y_train)
    
    mark_stop += 1
    
    if mark_stop == 1:
        break

  0%|                                                | 0/148576 [00:00<?, ?it/s]

7
user profile:         DegreeType  WorkHistoryCount  TotalYearsExperience  CurrentlyEmployed  \
50231           1                 2                  13.0                  1   

       ManagedOthers  ManagedHowMany  
50231              0               0  
user feature:  [[ 1.          2.         13.          1.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.467288    0.          0.          0.
   0.69007561  0.          0.          0.          0.          0.
   0.          0.          0.55266407  0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.        ]]
jobs applied by the user:  [309823 703889 566574 481216]
combine user_feature and embeded job 4
Result X_tr

In [ ]:
# Get user profile
user = user_set[user_set.UserID==u_id][["DegreeType", "WorkHistoryCount", 
                                            "TotalYearsExperience", "CurrentlyEmployed", 
                                            "ManagedOthers", "ManagedHowMany"]]
user

DegreeType  WorkHistoryCount  TotalYearsExperience  CurrentlyEmployed  \
50231           1                 2                  13.0                  1   

       ManagedOthers  ManagedHowMany  
50231              0               0

In [ ]:
u_id

7

In [ ]:
# Get embedded feature for work_history of this user
u_idx = user.index.values[0]
print(u_idx)
word_history_tf_matrix[u_idx,:].toarray()

50231


array([[0.        , 0.        , 0.        , 0.        , 0.        ,
        0.        , 0.        , 0.        , 0.        , 0.        ,
        0.        , 0.        , 0.        , 0.        , 0.        ,
        0.        , 0.        , 0.        , 0.        , 0.        ,
        0.        , 0.        , 0.        , 0.        , 0.        ,
        0.        , 0.467288  , 0.        , 0.        , 0.        ,
        0.69007561, 0.        , 0.        , 0.        , 0.        ,
        0.        , 0.        , 0.        , 0.55266407, 0.        ,
        0.        , 0.        , 0.        , 0.        , 0.        ,
        0.        , 0.        , 0.        , 0.        , 0.        ]])

In [ ]:
# Get user_feature
user_feature = np.concatenate((user.values, word_history_tf_matrix[u_idx,:].toarray()),axis=1)
print('user feature: ', user_feature)

user feature:  [[ 1.          2.         13.          1.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.467288    0.          0.          0.
   0.69007561  0.          0.          0.          0.          0.
   0.          0.          0.55266407  0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.        ]]


In [ ]:
groups.head()

UserID   JobID  label  City  State  Country
0              7  309823      1   1.0    1.0      1.0
1              7  703889      1   1.0    1.0      1.0
2              7  566574      0   0.0    0.0      1.0
3              7  481216      0   0.0    0.0      1.0
4              9  809208      1   1.0    1.0      1.0
...          ...     ...    ...   ...    ...      ...
2081335  1472085  209482      0   0.0    0.0      1.0
2081336  1472090  209535      1   1.0    1.0      1.0
2081337  1472090  254881      1   1.0    1.0      1.0
2081338  1472090  999294      0   0.0    0.0      1.0
2081339  1472090  354025      0   0.0    0.0      1.0

[494017 rows x 6 columns]

In [ ]:
# Get list of jobs 
#job_id_list = group.JobID.values
job_id_list = train_data[train_data['UserID']==7]['JobID'].to_list()
jobs = job_set[job_set.JobID.isin(job_id_list)]
print('jobs applied by the user: ', job_id_list)

jobs applied by the user:  [309823, 703889, 566574, 481216]


In [ ]:
jobs

JobID  WindowID                                              Title  \
333811  566574         2                            Cost Accounting Manager   
441578  309823         3                                             Teller   
488867  703889         3  Customer Service Representative, Now Accepting...   
599252  481216         4                            Analog Product Engineer   

                                              Description  \
333811  About UsStanley Black & Decker Corporation is ...   
441578  Our vision is to satisfy all our customers  fi...   
488867  How's your Quality of Life?• Are you looking f...   
599252  Volt is a global provider of talent, technolog...   

                                             Requirements              City  \
333811                                          see above          Marietta   
441578  * Basic Qualifications: 1+ years experience in...           Roanoke   
488867  To be considered for the opportunity to improv...           Roanoke   
599252  Qualifications:o Bachelor's Degree in Electric...  Colorado Springs   

       State Country     Zip5                StartDate              EndDate  \
333811    GA      US           2012-03-20 16:07:08.287  2012-04-19 23:59:59   
441578    VA      US           2012-04-20 19:29:22.367  2012-05-19 23:59:59   
488867    VA      US            2012-04-04 04:39:35.42  2012-05-03 23:59:59   
599252    CO      US  80920.0  2012-05-15 14:06:27.353  2012-06-14 23:59:59   

                                                     word  
333811  Cost Accounting ManagerAbout UsStanley Black &...  
441578  TellerOur vision is to satisfy all our custome...  
488867  Customer Service Representative, Now Accepting...  
599252  Analog Product EngineerVolt is a global provid...

In [ ]:
j_idx = jobs.index.values
f = []

for i in j_idx:
    feature = np.concatenate((user_feature, tfidf_matrix[i,:].toarray()), axis=1).reshape(156,).tolist()
    f.append(feature)
print('combine user_feature and embeded job', len(f))
    
    

combine user_feature and embeded job 4


In [ ]:
# each element in f is  a combine feature
len(f[0])

156

In [ ]:

group[["City","State","Country"]].values.shape

(4, 3)

In [ ]:
np.array(f).shape

(4, 156)

In [ ]:
# Cannot add Country => feature became (1, 159) and cannot concat to X_train
feature = np.concatenate((group[["City","State"]].values, np.array(f)),axis=1)

In [ ]:
feature.shape

(4, 158)

In [ ]:
X_train.shape

(1, 158)

In [ ]:
X_train = np.concatenate((X_train, feature), axis=0)

# Try verion with 159 

In [ ]:
# Try with small iteration

groups = train_data.groupby("UserID")
X_train = np.zeros((1,159)) # Include Country matching => feature vector (1,159)
Y_train = []
mark_stop = 0

for u_id, group in tqdm(groups):
    print(u_id)
    user = user_set[user_set.UserID==u_id][["DegreeType", "WorkHistoryCount", 
                                            "TotalYearsExperience", "CurrentlyEmployed", 
                                            "ManagedOthers", "ManagedHowMany"]]
    print('user profile: ', user)
    
    u_idx = user.index.values[0]
    
    user_feature = np.concatenate((user.values, word_history_tf_matrix[u_idx,:].toarray()),axis=1)
    print('user feature: ', user_feature)
        
    job_id_list = group.JobID.values
    jobs = job_set[job_set.JobID.isin(job_id_list)]
    print('Number of jobs applied by the user: ', len(job_id_list))
    
    j_idx = jobs.index.values
    f = []
    
    for i in j_idx:
        feature = np.concatenate((user_feature, tfidf_matrix[i,:].toarray()), axis=1).reshape(156,).tolist()
        f.append(feature)
    print('combine user_feature and embeded job', len(f))
    print('shape of vector f:', np.array(f).shape)
    
    print('group[["City","State", "Country"]].values', group[["City","State", "Country"]].values.shape)
    
    feature = np.concatenate((group[["City","State", "Country"]].values, np.array(f)),axis=1)
    
    print('Shape of feature vector: ', feature.shape)
    print('Shape of X_train', X_train.shape)
    
    X_train = np.concatenate((X_train, feature), axis=0)
    Y_train.extend(group.label.values.tolist())
    
    #print('Result X_train, Y_train:')
    #print(X_train)
    #print(Y_train)
    
    mark_stop += 1
    
    if mark_stop == 1:
        break

  0%|                                                | 0/148576 [00:00<?, ?it/s]

7
user profile:         DegreeType  WorkHistoryCount  TotalYearsExperience  CurrentlyEmployed  \
50231           1                 2                  13.0                  1   

       ManagedOthers  ManagedHowMany  
50231              0               0  
user feature:  [[ 1.          2.         13.          1.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.467288    0.          0.          0.
   0.69007561  0.          0.          0.          0.          0.
   0.          0.          0.55266407  0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.        ]]
Number of jobs applied by the user:  4
combine user_feature and embeded job 4
shape of vector f: (4, 156)
g

## Building training, testing vector

2 versions:
- including Country match (vector size: 159)
- excluding Country match (vector size: 158, similar to PJFNN)

#### Version with Country match (vector size: 159)

In [ ]:
# Version with Country match (vector size: 159)
groups = train_data.groupby("UserID")
X_train = np.zeros((1,159))
Y_train = []
for u_id, group in tqdm(groups):
    print('u_id:', u_id)
    user = user_set[user_set.UserID==u_id][["DegreeType", "WorkHistoryCount", 
                                            "TotalYearsExperience", "CurrentlyEmployed", 
                                            "ManagedOthers", "ManagedHowMany"]]
    u_idx = user.index.values[0]
    user_feature = np.concatenate((user.values, word_history_tf_matrix[u_idx,:].toarray()),axis=1)
    job_id_list = group.JobID.values
    jobs = job_set[job_set.JobID.isin(job_id_list)]
    j_idx = jobs.index.values
    f = []
    for i in j_idx:
        feature = np.concatenate((user_feature, tfidf_matrix[i,:].toarray()), axis=1).reshape(156,).tolist()
        f.append(feature)
        
    print('combine user_feature and embeded job', len(f))
    print('shape of vector f:', np.array(f).shape)
    
    print('group[["City","State", "Country"]].values', group[["City","State", "Country"]].values.shape)
    
    feature = np.concatenate((group[["City","State","Country"]].values, np.array(f)),axis=1)
    
    print('Shape of feature vector: ', feature.shape)
    print('Shape of X_train: ', X_train.shape)
    
    X_train = np.concatenate((X_train, feature), axis=0)
    Y_train.extend(group.label.values.tolist())

  0%|                                      | 20/148576 [00:00<23:47, 104.10it/s]

u_id: 7
combine user_feature and embeded job 4
shape of vector f: (4, 156)
group[["City","State", "Country"]].values (4, 3)
Shape of feature vector:  (4, 159)
Shape of X_train:  (1, 159)
u_id: 9
combine user_feature and embeded job 6
shape of vector f: (6, 156)
group[["City","State", "Country"]].values (6, 3)
Shape of feature vector:  (6, 159)
Shape of X_train:  (5, 159)
u_id: 16
combine user_feature and embeded job 4
shape of vector f: (4, 156)
group[["City","State", "Country"]].values (4, 3)
Shape of feature vector:  (4, 159)
Shape of X_train:  (11, 159)
u_id: 26
combine user_feature and embeded job 8
shape of vector f: (8, 156)
group[["City","State", "Country"]].values (8, 3)
Shape of feature vector:  (8, 159)
Shape of X_train:  (15, 159)
u_id: 44
combine user_feature and embeded job 2
shape of vector f: (2, 156)
group[["City","State", "Country"]].values (2, 3)
Shape of feature vector:  (2, 159)
Shape of X_train:  (23, 159)
u_id: 64
combine user_feature and embeded job 6
shape of ve

  0%|                                      | 45/148576 [00:00<21:09, 116.99it/s]

combine user_feature and embeded job 6
shape of vector f: (6, 156)
group[["City","State", "Country"]].values (6, 3)
Shape of feature vector:  (6, 159)
Shape of X_train:  (81, 159)
u_id: 254
combine user_feature and embeded job 4
shape of vector f: (4, 156)
group[["City","State", "Country"]].values (4, 3)
Shape of feature vector:  (4, 159)
Shape of X_train:  (87, 159)
u_id: 269
combine user_feature and embeded job 2
shape of vector f: (2, 156)
group[["City","State", "Country"]].values (2, 3)
Shape of feature vector:  (2, 159)
Shape of X_train:  (91, 159)
u_id: 272
combine user_feature and embeded job 6
shape of vector f: (6, 156)
group[["City","State", "Country"]].values (6, 3)
Shape of feature vector:  (6, 159)
Shape of X_train:  (93, 159)
u_id: 286
combine user_feature and embeded job 8
shape of vector f: (8, 156)
group[["City","State", "Country"]].values (8, 3)
Shape of feature vector:  (8, 159)
Shape of X_train:  (99, 159)
u_id: 294
combine user_feature and embeded job 2
shape of ve

  0%|                                      | 73/148576 [00:00<19:44, 125.36it/s]

...

 12%|████                              | 17986/148576 [12:31<2:44:12, 13.25it/s]

u_id: 182100
combine user_feature and embeded job 8
shape of vector f: (8, 156)
group[["City","State", "Country"]].values (8, 3)
Shape of feature vector:  (8, 159)
Shape of X_train:  (67507, 159)
u_id: 182106
combine user_feature and embeded job 2
shape of vector f: (2, 156)
group[["City","State", "Country"]].values (2, 3)
Shape of feature vector:  (2, 159)
Shape of X_train:  (67515, 159)
u_id: 182130
combine user_feature and embeded job 4
shape of vector f: (4, 156)
group[["City","State", "Country"]].values (4, 3)
Shape of feature vector:  (4, 159)
Shape of X_train:  (67517, 159)


 12%|████                              | 17987/148576 [12:31<1:30:58, 23.92it/s]

u_id: 182141
combine user_feature and embeded job 7
shape of vector f: (7, 156)
group[["City","State", "Country"]].values (8, 3)


ValueError: all the input array dimensions for the concatenation axis must match exactly, but along dimension 0, the array at index 0 has size 8 and the array at index 1 has size 7

In [ ]:
# Debug for user: 182141

groups = train_data.groupby("UserID")
X_train = np.zeros((1,159)) # Include Country matching => feature vector (1,159)
Y_train = []

u_id = 182141
user = user_set[user_set.UserID==u_id][["DegreeType", "WorkHistoryCount", 
                                            "TotalYearsExperience", "CurrentlyEmployed", 
                                            "ManagedOthers", "ManagedHowMany"]]
print('user profile: ', user)
    
u_idx = user.index.values[0]
    
user_feature = np.concatenate((user.values, word_history_tf_matrix[u_idx,:].toarray()),axis=1)
print('user feature: ', user_feature)
        


user profile:        DegreeType  WorkHistoryCount  TotalYearsExperience  CurrentlyEmployed  \
3201           4                 5                  19.0                  0   

      ManagedOthers  ManagedHowMany  
3201              0               0  
user feature:  [[ 4.  5. 19.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.]]


In [ ]:
# Get list of jobs 
#job_id_list = group.JobID.values
job_id_list = train_data[train_data['UserID']==u_id]['JobID'].to_list()
jobs = job_set[job_set.JobID.isin(job_id_list)]
print('jobs applied by the user: ', job_id_list)

jobs applied by the user:  [50860, 597394, 821506, 758611, 48199, 694162, 592961, 592961]


In [ ]:
train_data[train_data['UserID']==u_id]

UserID   JobID  label  City  State  Country
227840  182141   50860      1   0.0    1.0      1.0
227841  182141  597394      1   0.0    0.0      1.0
227842  182141  821506      1   0.0    0.0      1.0
227843  182141  758611      1   0.0    0.0      1.0
227844  182141   48199      0   0.0    0.0      1.0
227845  182141  694162      0   0.0    0.0      1.0
227846  182141  592961      0   0.0    0.0      1.0
227847  182141  592961      0   0.0    0.0      1.0

In [ ]:
j_idx

array([ 13090, 139634, 177783, 192444, 545164, 881673, 892217])

In [ ]:
j_idx = jobs.index.values
f = []

for i in j_idx:
    feature = np.concatenate((user_feature, tfidf_matrix[i,:].toarray()), axis=1).reshape(156,).tolist()
    f.append(feature)
print('combine user_feature and embeded job', len(f))
    
    

combine user_feature and embeded job 7


In [ ]:
group[["City","State","Country"]].values


array([[0., 1., 1.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.]])

In [ ]:
group[["City","State","Country"]].values.shape

(8, 3)

In [ ]:
np.array(f).shape

(2, 156)

In [ ]:
feature = np.concatenate((group[["City","State","Country"]].values, np.array(f)),axis=1)


ValueError: all the input array dimensions for the concatenation axis must match exactly, but along dimension 0, the array at index 0 has size 8 and the array at index 1 has size 2

In [ ]:
train_data[train_data.duplicated()==True]

UserID   JobID  label  City  State  Country
227847  182141  592961      0   0.0    0.0      1.0

In [ ]:
# Test again with this user after drop duplicated application in trian_data
# Version with Country match (vector size: 159)
groups = train_data.groupby("UserID")
X_train = np.zeros((1,159))
Y_train = []
u_id = 182141
user = user_set[user_set.UserID==u_id][["DegreeType", "WorkHistoryCount", 
                                        "TotalYearsExperience", "CurrentlyEmployed", 
                                        "ManagedOthers", "ManagedHowMany"]]
u_idx = user.index.values[0]
user_feature = np.concatenate((user.values, word_history_tf_matrix[u_idx,:].toarray()),axis=1)

job_id_list = train_data[train_data['UserID']==u_id]['JobID'].to_list()
jobs = job_set[job_set.JobID.isin(job_id_list)]
print('jobs applied by the user: ', job_id_list)
    
#     job_id_list = group.JobID.values
#     jobs = job_set[job_set.JobID.isin(job_id_list)]
j_idx = jobs.index.values
f = []
for i in j_idx:
    feature = np.concatenate((user_feature, tfidf_matrix[i,:].toarray()), axis=1).reshape(156,).tolist()
    f.append(feature)

print('combine user_feature and embeded job', len(f))
print('shape of vector f:', np.array(f).shape)

print('group[["City","State", "Country"]].values', group[["City","State", "Country"]].values.shape)

feature = np.concatenate((group[["City","State","Country"]].values, np.array(f)),axis=1)

print('Shape of feature vector: ', feature.shape)
print('Shape of X_train: ', X_train.shape)

X_train = np.concatenate((X_train, feature), axis=0)
Y_train.extend(group.label.values.tolist())

jobs applied by the user:  [50860, 597394, 821506, 758611, 48199, 694162, 592961]
combine user_feature and embeded job 7
shape of vector f: (7, 156)
group[["City","State", "Country"]].values (2, 3)


ValueError: all the input array dimensions for the concatenation axis must match exactly, but along dimension 0, the array at index 0 has size 2 and the array at index 1 has size 7

In [ ]:
X_train = np.concatenate((X_train, feature), axis=0)
Y_train.extend(group.label.values.tolist())

In [ ]:
X_train.shape, len(Y_train)

In [ ]:
# Test data: Version with Country match (vector size: 159)
groups = test_data.groupby("UserID")
X_test = np.zeros((1,159))
Y_test = []
for u_id, group in tqdm(groups):
    user = user_set[user_set.UserID==u_id][["DegreeType", "WorkHistoryCount", 
                                            "TotalYearsExperience", "CurrentlyEmployed", 
                                            "ManagedOthers", "ManagedHowMany"]]
    u_idx = user.index.values[0]
    user_feature = np.concatenate((user.values, word_history_tf_matrix[u_idx,:].toarray()),axis=1)
    job_id_list = group.JobID.values
    jobs = job_set[job_set.JobID.isin(job_id_list)]
    j_idx = jobs.index.values
    f = []
    for i in j_idx:
        feature = np.concatenate((user_feature, tfidf_matrix[i,:].toarray()), axis=1).reshape(156,).tolist()
        f.append(feature)
    feature = np.concatenate((group[["City","State", "Country"]].values, np.array(f)),axis=1)
    X_test = np.concatenate((X_test, feature), axis=0)
    Y_test.extend(group.label.values.tolist())

100%|███████████████████████████████████████| 3716/3716 [00:49<00:00, 75.24it/s]


In [ ]:
X_test.shape, len(Y_test)

((15737, 159), 15736)

In [ ]:
# Export train and test dataset to folder cb12-nn
#np.save("./output_baseline/X_train.npy",X_train[1:,])
#np.save("./output_baseline/Y_train.npy",np.array(Y_train))
np.save("./output_baseline/X_test.npy",X_test[1:,])
np.save("./output_baseline/Y_test.npy",np.array(Y_test))

#### Version WITHOUT Country match (vector size: 158) - BACKUP

In [ ]:
# Version WITHOUT Country match (vector size: 158)
groups = train_data.groupby("UserID")
X_train_158 = np.zeros((1,158))
Y_train_158 = []
for u_id, group in tqdm(groups):
    user = user_set[user_set.UserID==u_id][["DegreeType", "WorkHistoryCount", 
                                            "TotalYearsExperience", "CurrentlyEmployed", 
                                            "ManagedOthers", "ManagedHowMany"]]
    u_idx = user.index.values[0]
    user_feature = np.concatenate((user.values, word_history_tf_matrix[u_idx,:].toarray()),axis=1)
    job_id_list = group.JobID.values
    jobs = job_set[job_set.JobID.isin(job_id_list)]
    j_idx = jobs.index.values
    f = []
    for i in j_idx:
        feature = np.concatenate((user_feature, tfidf_matrix[i,:].toarray()), axis=1).reshape(156,).tolist()
        f.append(feature)
    feature = np.concatenate((group[["City","State"]].values, np.array(f)),axis=1)
    X_train_158 = np.concatenate((X_train_158, feature), axis=0)
    Y_train_158.extend(group.label.values.tolist())

 12%|████                              | 17987/148576 [13:12<1:35:54, 22.69it/s]


ValueError: all the input array dimensions for the concatenation axis must match exactly, but along dimension 0, the array at index 0 has size 8 and the array at index 1 has size 7

In [ ]:
# Version WITHOUT Country match (vector size: 158)
groups = test_data.groupby("UserID")
X_test_158 = np.zeros((1,158))
Y_test_158 = []
for u_id, group in tqdm(groups):
    user = user_set[user_set.UserID==u_id][["DegreeType", "WorkHistoryCount", 
                                            "TotalYearsExperience", "CurrentlyEmployed", 
                                            "ManagedOthers", "ManagedHowMany"]]
    u_idx = user.index.values[0]
    user_feature = np.concatenate((user.values, word_history_tf_matrix[u_idx,:].toarray()),axis=1)
    job_id_list = group.JobID.values
    jobs = job_set[job_set.JobID.isin(job_id_list)]
    j_idx = jobs.index.values
    f = []
    for i in j_idx:
        feature = np.concatenate((user_feature, tfidf_matrix[i,:].toarray()), axis=1).reshape(156,).tolist()
        f.append(feature)
    feature = np.concatenate((group[["City","State"]].values, np.array(f)),axis=1)
    X_test_158 = np.concatenate((X_test_158, feature), axis=0)
    Y_test_158.extend(group.label.values.tolist())

100%|███████████████████████████████████████| 3716/3716 [00:49<00:00, 74.47it/s]


In [ ]:
X_test.shape, len(Y_test)

((15737, 158), 15736)